In [1]:
# coding: utf-8

from __future__ import print_function
__version__ = 2

%matplotlib inline

import librosa.display
from matplotlib import pyplot as plt
import numpy as np
import os
import pandas as pd

In [72]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, MinMaxScaler
from tensorflow.keras.utils import to_categorical

In [73]:
from numpy.random import seed
seed(1)
import tensorflow
tensorflow.keras.__version__

'2.2.4-tf'

In [2]:
df = pd.read_csv('intonation.csv')
df1 = df.head(10)
df[' arrangement_id'].nunique()
#df1

745

In [3]:
perf_id = '1003854545_1795973291'
vocals_pyin_directory = os.path.join("vocals_pyin")
pyin = np.load(os.path.join(vocals_pyin_directory, perf_id + ".npy"))

In [4]:
pyin

array([285.52908348, 285.25146357, 285.38110623, ..., 388.98463997,
       375.06249064, 351.63650959])

In [5]:
y, sr = librosa.load('vocal_tracks/'+perf_id+'.m4a')
len(y)

3702400

In [6]:
list(y)

[0.0058004446,
 0.008748933,
 0.0074954275,
 0.007891108,
 0.0077855433,
 0.007674067,
 0.0075453883,
 0.0075631384,
 0.007464144,
 0.0075394283,
 0.0073755966,
 0.0076409946,
 0.0075355885,
 0.0075598895,
 0.007415516,
 0.007306206,
 0.007052365,
 0.006918091,
 0.006789403,
 0.0066800807,
 0.0064853933,
 0.006554677,
 0.006309054,
 0.006302975,
 0.006239784,
 0.0060196766,
 0.0058578565,
 0.005791086,
 0.005573893,
 0.0055348612,
 0.005515762,
 0.0056473096,
 0.0055112797,
 0.005472718,
 0.005478184,
 0.005134813,
 0.0049664467,
 0.0050761895,
 0.0048874393,
 0.0050328183,
 0.0052380287,
 0.0052529187,
 0.0053228796,
 0.0053673116,
 0.0054751537,
 0.005661104,
 0.0056715948,
 0.00588678,
 0.005803753,
 0.005462857,
 0.005537055,
 0.005436231,
 0.005303271,
 0.0056668855,
 0.005625139,
 0.005608496,
 0.0058670132,
 0.0056871986,
 0.0057379766,
 0.005924208,
 0.005785934,
 0.005796984,
 0.0058759456,
 0.005800043,
 0.0058375993,
 0.005914058,
 0.0059229117,
 0.005819344,
 0.0058419444,


In [7]:
vocals = []
ind = 0
for perf in df1['performance_id']:
    print(ind)
    ind=ind+1
    y, sr = librosa.load('vocal_tracks/'+perf+'.m4a')
    vocal_array = list(y)
    for i in range(7000000-len(vocal_array)):
        vocal_array.append(0)
    vocals_pyin_directory = os.path.join("vocals_pyin")
    pyin = np.load(os.path.join(vocals_pyin_directory, perf + ".npy"))
    if (len(pyin) == 5160):
        for py in list(pyin):
            vocal_array.append(py)
            vocals.append(vocal_array)

0
1
2
3
4
5
6
7
8
9


In [11]:
pitches, magnitudes = librosa.core.piptrack(y=y, sr=sr, S=None, n_fft= 2048, hop_length=256, fmin=150, fmax=500, threshold=0.75)
shape = np.shape(pitches)
shape

(1025, 24295)

In [7]:
def extract_max(pitches,magnitudes, shape):
    new_pitches = []
    new_magnitudes = []
    for i in range(0, shape[1]):
        new_pitches.append(np.max(pitches[:,i]))
        new_magnitudes.append(np.max(magnitudes[:,i]))
    return (new_pitches,new_magnitudes)

In [8]:
def smooth(x,window_len=11,window='hanning'):
        if window_len<3:
                return x
        if not window in ['flat', 'hanning', 'hamming', 'bartlett', 'blackman']:
                raise ValueError
        s=np.r_[2*x[0]-x[window_len-1::-1],x,2*x[-1]-x[-1:-window_len:-1]]
        if window == 'flat': #moving average
                w=np.ones(window_len,'d')
        else:
                w=eval('np.'+window+'(window_len)')
        y=np.convolve(w/w.sum(),s,mode='same')
        return y[window_len:-window_len+1]

In [9]:
def set_variables(sample_f,duration,window_time,fmin,fmax,overlap):
    total_samples = sample_f * duration
    #There are sample_f/1000 samples / ms
    #windowsize = number of samples in one window
    window_size = sample_f/1000 * window_time
    hop_length = total_samples / window_size
    #Calculate number of windows needed
    needed_nb_windows = total_samples / (window_size - overlap)
    n_fft = needed_nb_windows * 2.0
    return total_samples, window_size, needed_nb_windows, n_fft, hop_length

In [10]:
def analyse(y,sr,n_fft,hop_length,fmin,fmax):
    pitches, magnitudes = librosa.core.piptrack(y=y, sr=sr, S=None, n_fft= n_fft, hop_length=hop_length, fmin=fmin, fmax=fmax, threshold=0.75)
    shape = np.shape(pitches)
    #nb_samples = total_samples / hop_length
    nb_samples = shape[0]
    #nb_windows = n_fft / 2
    nb_windows = shape[1]
    pitches,magnitudes = extract_max(pitches, magnitudes, shape)

    pitches1 = smooth(pitches,window_len=5)
    pitches2 = smooth(pitches,window_len=20)
    pitches3 = smooth(pitches,window_len=30)
    pitches4 = smooth(pitches,window_len=40)
    
#    plot(pitches1, 'pitches1')
#    plot(pitches2, 'pitches2')
#    plot(pitches3, 'pitches3')
#    plot(pitches4, 'pitches4')
#   plot(magnitudes, 'magnitudes')
#    plot( y, 'audio')
    return pitches1

In [11]:
#Set all wanted variables
path = 'vocal_tracks/'+perf_id+'.m4a'
path2 = '188let_it_go.m4a'
    #we want a sample frequency of 16 000
sample_f = 22050
    #The duration of the voice sample
duration = 220
    #We want a windowsize of 30 ms
window_time = 30
fmin = 200
fmax = 500
    #We want an overlap of 10 ms
overlap = 10
total_samples, window_size, needed_nb_windows, n_fft, hop_length = set_variables(sample_f, duration, window_time, fmin, fmax, overlap)


    # y = audio time series
    # sr = sampling rate of y
y, sr = librosa.load(path, sr=sample_f, duration=duration)
#y1, sr1 = librosa.load(path2, sr=sample_f, duration=27)
n_fft =2048
n_fft = int(n_fft)
hop_length = int(hop_length)


pitches2 = analyse(y, sr, n_fft, hop_length, fmin, fmax)


In [12]:
len(pitches2)

505

In [13]:
pitches2

array([  0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        , 113.47080994, 226.94161987, 113.47080994,
        99.70288849, 199.40577698, 213.99898529, 228.5921936 ,
       195.52475739, 244.90187836, 332.17979431, 334.82593536,
       246.5766983 , 164.53472137, 168.55476379,  84.2773819 ,
        85.59226227, 290.66799927, 324.55921173, 119.48347473,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        , 116.49555206,
       300.91340637, 353.94969177, 385.7203064 , 330.76740265,
       191.16609192, 153.17431641,  76.5871582 ,   0.        ,
         0.        , 124.71060944, 249.42121887, 124.71

In [23]:
import os
sample_f = 22050
    #The duration of the voice sample
duration = 220
    #We want a windowsize of 30 ms
window_time = 30
fmin = 200
fmax = 500
    #We want an overlap of 10 ms
overlap = 10
total_samples, window_size, needed_nb_windows, n_fft, hop_length = set_variables(sample_f, duration, window_time, fmin, fmax, overlap)
vocals = []
ind = 0
for perf in os.listdir('vocal_tracks'):
    print(ind)
    ind=ind+1
    y, sr = librosa.load('vocal_tracks/'+perf)
    n_fft =2048
    n_fft = int(n_fft)
    hop_length = int(hop_length)
    pitches2 = analyse(y, sr, n_fft, hop_length, fmin, fmax)
    pitches = list(pitches2)[:450]
    vocals.append(pitches)
    perf_id=perf.split('.')[0]
    vocals.append(perf_id)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700


In [49]:
for perf in os.listdir('vocal_tracks'):
    print(perf)

349476135_1625374877.m4a
206130952_2055553391.m4a
966886243_1820248283.m4a
370240075_2100123703.m4a
646830040_1765257451.m4a
208106085_2174565362.m4a
424237503_1908580608.m4a
1243564299_1728162466.m4a
459935119_1886186883.m4a
635751142_2085033788.m4a
503829359_2152771296.m4a
901967954_2078282428.m4a
1117230404_1579003468.m4a
956199260_2023213229.m4a
449420732_2036722042.m4a
1007166954_2129697117.m4a
549783780_1546398849.m4a
165803199_1647799585.m4a
1115383341_1517843924.m4a
1288532602_2087382293.m4a
1557706134_1953280062.m4a
1407351096_1691027711.m4a
1371412711_2227253903.m4a
156090141_1779095366.m4a
499166693_2332656375.m4a
1480570110_2073332810.m4a
507137820_2225545415.m4a
32642150_1713679340.m4a
1509096108_2274042958.m4a
1697453486_2190403389.m4a
589586259_1734797996.m4a
118700482_2312533706.m4a
414865157_1682817012.m4a
86323464_1798797890.m4a
929571874_1839889087.m4a
1455951929_1775471387.m4a
314047592_1739655139.m4a
1009479994_1691485249.m4a
347200007_1652137670.m4a
1533474740_194

1574472167_1976463570.m4a
116803638_1524695608.m4a
329910068_1528834120.m4a
1249430297_2006631797.m4a
550330631_1644875092.m4a
1080337722_1795724671.m4a
414865157_1949640927.m4a
900873834_1910495319.m4a
478219628_2174062330.m4a
270869302_1816197132.m4a
1279706077_1970232215.m4a
395742875_1614874926.m4a
850976090_1563380712.m4a
1662945134_2131132195.m4a
1333258860_1687874495.m4a
907586203_2252812625.m4a
402750685_1932656165.m4a
1047325519_2231292133.m4a
41845084_1862237809.m4a
1708433342_2333590171.m4a
921817340_1866373871.m4a
1517751987_1886053391.m4a
1376074104_1623738057.m4a
1225582710_2311920156.m4a
210780537_2219949488.m4a
1469571873_1800121922.m4a
349625996_2242712660.m4a
689020863_1864847488.m4a
1440644472_1750654981.m4a
913936875_1944645429.m4a
552542860_1721092204.m4a
1381173982_1644615773.m4a
1451583234_1822386227.m4a
1418418930_1703945567.m4a
349805939_1903888304.m4a
843790239_2055897686.m4a
1413399470_1697255337.m4a
1254353908_1748193035.m4a
403593369_1937582936.m4a
13582588

In [36]:
vocals2=vocals
for i in range(0,len(vocals2),2):
    vocals2[i].append(vocals2[i+1])
vocals2

[[0.0,
  0.0,
  57.03999710083007,
  114.07999420166016,
  57.03999710083009,
  0.0,
  0.0,
  0.0,
  96.54794311523436,
  193.09588623046875,
  96.5479431152344,
  97.55535888671874,
  195.1107177734375,
  215.2360076904297,
  332.43324279785156,
  311.8245391845703,
  97.07194519042972,
  0.0,
  0.0,
  92.18911743164061,
  238.35975646972656,
  258.7961120605469,
  230.30721282958984,
  235.93939971923828,
  177.47753143310547,
  166.8340301513672,
  215.2283172607422,
  107.61415863037112,
  0.0,
  0.0,
  0.0,
  75.9060592651367,
  240.49324798583984,
  341.86930084228516,
  265.88309478759766,
  88.60098266601564,
  75.04652404785155,
  209.64177322387695,
  252.79310607910156,
  235.81101989746094,
  255.00322723388672,
  294.84316635131836,
  315.8861312866211,
  312.9758605957031,
  309.99342346191406,
  331.1465835571289,
  271.07826232910156,
  95.3822708129883,
  0.0,
  50.09590911865234,
  150.1811180114746,
  209.61233139038086,
  169.06494522094727,
  59.537822723388686,
  

In [47]:
new_df = pd.DataFrame(vocals2)
new_df=new_df.dropna(how='any')

In [48]:

new_df = new_df.drop(451, axis=1)
new_df = new_df.rename(columns={450:'performance_id'})
new_df.head()

0  1        2        3        4        5        6        7        8  \
0   0  0    57.04   114.08    57.04        0        0        0  96.5479   
2   0  0        0        0        0        0        0        0        0   
4   0  0        0        0        0        0        0        0   116.77   
6   0  0  84.0009  168.002  84.0009  69.5322  139.064  69.5322        0   
10  0  0        0        0        0        0        0        0  95.4433   

          9  ...      441      442      443      444      445      446  \
0   193.096  ...  69.0322  92.4566  184.913  92.4566        0        0   
2         0  ...  258.082  103.287        0        0        0  97.1433   
4    233.54  ...  270.209  87.2102  100.479  307.158  410.003  385.301   
6         0  ...        0        0  100.602  323.276  443.864  320.309   
10  190.887  ...        0        0        0        0        0        0   

        447      448      449        performance_id  
0         0  86.1391  172.278  349476135_1625374877  
2   304.433  317.436  214.877  206130952_2055553391  
4   354.047  346.089  260.816  966886243_1820248283  
6   99.1187        0  75.9618  370240075_2100123703  
10        0        0        0  208106085_2174565362  

[5 rows x 451 columns]

In [46]:
new_df

{450: 'performance_id'}

In [49]:
df=df[['performance_id',' arrangement_id']]

In [50]:
df_vocals = pd.merge(new_df,df, on='performance_id')
df_vocals.head()

0  1        2        3        4        5        6        7        8  \
0  0  0    57.04   114.08    57.04        0        0        0  96.5479   
1  0  0        0        0        0        0        0        0        0   
2  0  0        0        0        0        0        0        0   116.77   
3  0  0  84.0009  168.002  84.0009  69.5322  139.064  69.5322        0   
4  0  0        0        0        0        0        0        0  95.4433   

         9  ...      442      443      444      445      446      447  \
0  193.096  ...  92.4566  184.913  92.4566        0        0        0   
1        0  ...  103.287        0        0        0  97.1433  304.433   
2   233.54  ...  87.2102  100.479  307.158  410.003  385.301  354.047   
3        0  ...        0  100.602  323.276  443.864  320.309  99.1187   
4  190.887  ...        0        0        0        0        0        0   

       448      449        performance_id    arrangement_id  
0  86.1391  172.278  349476135_1625374877   3769822_3769822  
1  317.436  214.877  206130952_2055553391   3770457_3770457  
2  346.089  260.816  966886243_1820248283   3770492_3770492  
3        0  75.9618  370240075_2100123703   3769643_3769643  
4        0        0  208106085_2174565362   3771377_3771377  

[5 rows x 452 columns]

In [60]:
df_vocals[' arrangement_id'].nunique()

668

In [66]:
arrang_list = df_vocals[' arrangement_id'].value_counts()
arrang_list = arrang_list[:40]
df_arrang = pd.DataFrame(arrang_list)
df_arrang = df_arrang.reset_index()
arrang = list(df_arrang['index'])
arrang

[' 3771478_3771478',
 ' 3771973_3771973',
 ' 3769643_3769643',
 ' 3771116_3771116',
 ' 3772190_3772190',
 ' 3771926_3771926',
 ' 3769415_3769415',
 ' 3770160_3770160',
 ' 3770803_3770803',
 ' 3769836_3769836',
 ' 3770948_3770948',
 ' 3770185_3770185',
 ' 3770106_3770106',
 ' 3769319_3769319',
 ' 3769411_3769411',
 ' 3772049_3772049',
 ' 3770602_3770602',
 ' 3770431_3770431',
 ' 3772019_3772019',
 ' 3771377_3771377',
 ' 3771107_3771107',
 ' 3772081_3772081',
 ' 3769477_3769477',
 ' 3771823_3771823',
 ' 3772221_3772221',
 ' 3769493_3769493',
 ' 3771611_3771611',
 ' 3769676_3769676',
 ' 3770322_3770322',
 ' 3771258_3771258',
 ' 3769841_3769841',
 ' 3771451_3771451',
 ' 3771723_3771723',
 ' 3770789_3770789',
 ' 3769730_3769730',
 ' 3769897_3769897',
 ' 3771860_3771860',
 ' 3769590_3769590',
 ' 3772088_3772088',
 ' 3771902_3771902']

In [69]:
df_v = df_vocals.loc[df_vocals[' arrangement_id'].isin(arrang)]

In [70]:
df_v[' arrangement_id'].nunique()

40

In [71]:
df_v.head()

0        1        2        3        4        5        6        7  \
3        0        0  84.0009  168.002  84.0009  69.5322  139.064  69.5322   
4        0        0        0        0        0        0        0        0   
5  346.357  115.452  115.984  343.904  444.904  446.717  473.446  362.736   
6        0        0  50.5963  151.372  150.955  50.1796        0  50.0303   
8        0        0        0        0        0        0        0        0   

         8        9  ...      442      443      444      445      446  \
3        0        0  ...        0  100.602  323.276  443.864  320.309   
4  95.4433  190.887  ...        0        0        0        0        0   
5  119.024        0  ...  284.019  396.936  429.341  416.365  312.804   
6  100.061  50.0303  ...   177.52  88.7602        0  75.4801  253.604   
8        0        0  ...  137.191  221.481  281.516  295.701    318.9   

       447      448      449         performance_id    arrangement_id  
3  99.1187        0  75.9618   370240075_2100123703   3769643_3769643  
4        0        0        0   208106085_2174565362   3771377_3771377  
5  104.374  118.766   354.02  1243564299_1728162466   3770185_3770185  
6  383.642  308.391  102.873   459935119_1886186883   3772221_3772221  
8  234.144   73.445        0   956199260_2023213229   3769477_3769477  

[5 rows x 452 columns]

In [74]:
X = df_v.drop('performance_id', axis=1).drop(' arrangement_id', axis =1)
y = df_v[' arrangement_id']
print(X.shape, y.shape)

(2065, 450) (2065,)


In [75]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, random_state=1, stratify=y)

In [76]:
X_scaler = MinMaxScaler().fit(X_train)
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

/anaconda3/lib/python3.7/site-packages/sklearn/preprocessing/data.py:334: DataConversionWarning: Data with input dtype float64, object were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


In [77]:
label_encoder = LabelEncoder()
label_encoder.fit(y_train)
encoded_y_train = label_encoder.transform(y_train)
encoded_y_test = label_encoder.transform(y_test)

In [78]:
y_train_categorical = to_categorical(encoded_y_train, num_classes = 40)
y_test_categorical = to_categorical(encoded_y_test,num_classes = 40)

In [103]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
model = Sequential()
model.add(Dense(units=50, activation='relu', input_dim=450))
#model.add(Dense(units=6, activation='relu'))
model.add(Dense(units=40, activation='softmax'))

In [104]:
model.compile(optimizer='adam',
              loss='categorical_crossentropy',
              metrics=['accuracy'])
model.summary()

Model: "sequential_5"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_12 (Dense)             (None, 50)                22550     
_________________________________________________________________
dense_13 (Dense)             (None, 40)                2040      
Total params: 24,590
Trainable params: 24,590
Non-trainable params: 0
_________________________________________________________________


In [105]:
model.fit(
    X_train_scaled,
    y_train_categorical,
    epochs=100,
    shuffle=True,
    verbose=2
)

Train on 1548 samples
Epoch 1/100
1548/1548 - 0s - loss: 3.3880 - accuracy: 0.1776
Epoch 2/100
1548/1548 - 0s - loss: 2.7951 - accuracy: 0.3676
Epoch 3/100
1548/1548 - 0s - loss: 2.2850 - accuracy: 0.5401
Epoch 4/100
1548/1548 - 0s - loss: 1.8159 - accuracy: 0.6602
Epoch 5/100
1548/1548 - 0s - loss: 1.4384 - accuracy: 0.7500
Epoch 6/100
1548/1548 - 0s - loss: 1.1241 - accuracy: 0.8314
Epoch 7/100
1548/1548 - 0s - loss: 0.9045 - accuracy: 0.8727
Epoch 8/100
1548/1548 - 0s - loss: 0.7467 - accuracy: 0.9076
Epoch 9/100
1548/1548 - 0s - loss: 0.6334 - accuracy: 0.9193
Epoch 10/100
1548/1548 - 0s - loss: 0.5371 - accuracy: 0.9360
Epoch 11/100
1548/1548 - 0s - loss: 0.4702 - accuracy: 0.9399
Epoch 12/100
1548/1548 - 0s - loss: 0.4010 - accuracy: 0.9548
Epoch 13/100
1548/1548 - 0s - loss: 0.3545 - accuracy: 0.9548
Epoch 14/100
1548/1548 - 0s - loss: 0.3137 - accuracy: 0.9664
Epoch 15/100
1548/1548 - 0s - loss: 0.2825 - accuracy: 0.9729
Epoch 16/100
1548/1548 - 0s - loss: 0.2527 - accuracy: 0.

In [106]:
model_loss, model_accuracy = model.evaluate(
    X_test_scaled, y_test_categorical, verbose=2)
print(
    f"Normal Neural Network - Loss: {model_loss}, Accuracy: {model_accuracy}")

517/1 - 0s - loss: 0.1234 - accuracy: 0.9439
Normal Neural Network - Loss: 0.233452001752285, Accuracy: 0.9439071416854858


In [93]:
encoded_predictions = model.predict_classes(X_test_scaled[:10])
prediction_labels = label_encoder.inverse_transform(encoded_predictions)

In [94]:
print(f"Predicted classes: {prediction_labels}")
print(f"Actual Labels: {list(y_test[:10])}")

Predicted classes: [' 3769643_3769643' ' 3772081_3772081' ' 3771973_3771973'
 ' 3772081_3772081' ' 3770803_3770803' ' 3771478_3771478'
 ' 3770431_3770431' ' 3771107_3771107' ' 3770160_3770160'
 ' 3771451_3771451']
Actual Labels: [' 3770948_3770948', ' 3772081_3772081', ' 3771973_3771973', ' 3772081_3772081', ' 3770803_3770803', ' 3771478_3771478', ' 3770431_3770431', ' 3771107_3771107', ' 3770322_3770322', ' 3771451_3771451']
